<a href="https://colab.research.google.com/github/Yassmina-Abdo/realtime-head-pose-estimation/blob/main/Notebooks/models.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#from google.colab import drive
#drive.mount('/content/drive')

## Liberaries

In [11]:
import pandas as pd
from sklearn.model_selection import train_test_split
import cv2
import mediapipe as mp
import numpy as np
import time
import pickle
from math import cos, sin

## Reading the prepared dataset and split it

In [12]:
path_local='../../Data/media_with_angles_low_normed.csv'
#path_drive='/content/drive/MyDrive/Head Pose Estimation ML Project/Dataset/Data/media_with_angles_low.csv'
data =pd.read_csv(path_local)
data.head(5)

x1        x2        x3        x4        x5        x6        x7  \
0 -0.236824 -0.006193 -0.224011 -0.147134  0.032246 -0.006193 -0.159947   
1  0.104239 -0.004250  0.056021 -0.076575 -0.016304 -0.016304  0.019859   
2  0.180066 -0.003883  0.180066  0.017758 -0.036345 -0.003883  0.115143   
3  0.000114 -0.015663  0.031668 -0.110324  0.000114  0.000114  0.063222   
4 -0.107980 -0.005590 -0.056785 -0.069583  0.020008  0.032807  0.058404   

         x8        x9       x10  ...      y463      y464      y465      y466  \
0 -1.133721 -0.159947 -0.121508  ...  0.034117 -0.785904 -0.747465 -0.709027   
1 -0.582855  0.007804 -0.004250  ...  0.030482 -0.680720 -0.656611 -0.632502   
2  0.028579  0.115143  0.071861  ...  0.047943 -0.525545 -0.482263 -0.460622   
3 -1.041159  0.078999  0.078999  ... -0.015938 -1.341195 -1.246533 -1.167649   
4 -0.799111  0.084002  0.109599  ...  0.043323 -0.852588 -0.814192 -0.775796   

       y467      y468  image_name       yaw     pitch      roll  
0 -0.849968 -0.901219  image03195  0.725284 -0.140406 -0.174674  
1 -0.801262 -0.825371  image03247 -0.233745 -0.116700  0.095809  
2 -0.633751 -0.698674  image03214 -1.330352  0.003072  0.362599  
3 -1.593625 -1.656732  image03238 -0.040907 -0.474087  0.019801  
4 -0.916582 -0.954978  image03236  0.205732 -0.241359 -0.150232  

[5 rows x 940 columns]

In [13]:
X = data.iloc[:,:-4]
X.head(1)

x1        x2        x3        x4        x5        x6        x7  \
0 -0.236824 -0.006193 -0.224011 -0.147134  0.032246 -0.006193 -0.159947   

         x8        x9       x10  ...      y459      y460      y461      y462  \
0 -1.133721 -0.159947 -0.121508  ...  0.008491 -0.029947  0.008491  0.021304   

       y463      y464      y465      y466      y467      y468  
0  0.034117 -0.785904 -0.747465 -0.709027 -0.849968 -0.901219  

[1 rows x 936 columns]

In [14]:
y = data.iloc[:,-3:]
y.head(1)

yaw     pitch      roll
0  0.725284 -0.140406 -0.174674

In [15]:
x_train, x_test, y_train, y_test = train_test_split(X.to_numpy(), y.to_numpy(), test_size=0.20, random_state=42, shuffle=True)

In [16]:
def draw_axis(img, pitch,yaw,roll, tdx=None, tdy=None, size = 50):

    yaw = -yaw
    if tdx != None and tdy != None:
        tdx = tdx
        tdy = tdy
    else:
        height, width = img.shape[:2]
        tdx = width /2
        tdy = height /2

    # X-Axis pointing to right. drawn in red
    x1 = size * (cos(yaw) * cos(roll)) + tdx
    y1 = size * (cos(pitch) * sin(roll) + cos(roll) * sin(pitch) * sin(yaw)) + tdy

    # Y-Axis | drawn in green
    #        v
    x2 = size * (-cos(yaw) * sin(roll)) + tdx
    y2 = size * (cos(pitch) * cos(roll) - sin(pitch) * sin(yaw) * sin(roll)) + tdy

    # Z-Axis (out of the screen) drawn in blue
    x3 = size * (sin(yaw)) + tdx
    y3 = size * (-cos(yaw) * sin(pitch)) + tdy

    cv2.line(img, (int(tdx), int(tdy)), (int(x1),int(y1)),(0,0,255),3)
    cv2.line(img, (int(tdx), int(tdy)), (int(x2),int(y2)),(0,255,0),3)
    cv2.line(img, (int(tdx), int(tdy)), (int(x3),int(y3)),(255,0,0),2)
    return img

## Load Trained Model

In [17]:
pkl_filename='../../SavedModels/model_svr.pkl'
with open(pkl_filename, 'rb') as file:
    pretrained_model = pickle.load(file)

## Real Time Test

In [18]:
mp_face_mesh = mp.solutions.face_mesh
face_mesh = mp_face_mesh.FaceMesh(min_detection_confidence=0.5, min_tracking_confidence=0.5)
mp_drawing = mp.solutions.drawing_utils
drawing_spec = mp_drawing.DrawingSpec(thickness=1, circle_radius=1)

cap = cv2.VideoCapture(0)
i = 0
while cap.isOpened():
    success, image = cap.read()
    start = time.time()
    image = cv2.cvtColor(cv2.flip(image, 1), cv2.COLOR_BGR2RGB)
    image.flags.writeable = False
    results = face_mesh.process(image)
    image.flags.writeable = True
    # Convert the color space from RGB to BGR
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
    img_h, img_w, img_c = image.shape
    face_2d, x_points,  y_points=[],[],[]
  
    if results.multi_face_landmarks:   
        for face_landmarks in results.multi_face_landmarks:
            for idx, lm in enumerate(face_landmarks.landmark):
                if idx == 1 :
                    nose_2d = (lm.x * img_w, lm.y * img_h)
                    nose_3d = (lm.x * img_w, lm.y * img_h, lm.z * 3000)
                elif idx == 428 :  chin_2d = (lm.x * img_w, lm.y * img_h)      
                x, y = int(lm.x * img_w), int(lm.y * img_h)
                x_points.append(x) 
                y_points.append(y) 
                face_2d.append([x, y])
                
        # Convert it to the NumPy array
        distX =   chin_2d[0]-nose_2d[0] 
        distY = chin_2d[1]  -nose_2d[1]
        dist = (distX**2 + distY**2)**0.5
        
        face_2d = np.array(face_2d, dtype=np.float64)
        x_point=np.array(np.transpose(x_points).astype('float'),dtype=np.float64).reshape(1,-1)
        y_point=np.array(np.transpose(y_points).astype('float'),dtype=np.float64).reshape(1,-1)
        x_point = (x_point-nose_2d[0])/dist
        y_point = (y_point-nose_2d[1])/dist
        new_data = np.concatenate((x_point,y_point),axis=1)

        # Load pretrained model
        angles = pretrained_model.predict(new_data) #yaw , pitch , roll
        #angle_yaw =pretrained_GB_yaw_model.predict(new_data)
        #angle_pitch =pretrained_GB_pitch_model.predict(new_data)
        #angle_roll =pretrained_GB_roll_model.predict(new_data)
        x,y,z = angles[0][0],angles[0][1], angles[0][2]

        image = draw_axis(image,y,-x,-z,int(nose_2d[0]),int(nose_2d[1]))
        # Add the text on the image      
        cv2.putText(image, "x: " + str(np.round(x,2)), (500, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 0, 255), 2)
        cv2.putText(image, "y: " + str(np.round(y,2)), (500, 100), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 0, 255), 2)
        cv2.putText(image, "z: " + str(np.round(z,2)), (500, 150), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 0, 255), 2)

        end = time.time()
        totalTime = end - start
        fps = 1 / totalTime

        cv2.putText(image, f'FPS: {int(fps)}', (20,450), cv2.FONT_HERSHEY_SIMPLEX, 1.5, (0,255,0), 2)
        mp_drawing.draw_landmarks(
                    image=image,
                    landmark_list=face_landmarks,
                    connections=mp_face_mesh.FACEMESH_CONTOURS,
                    landmark_drawing_spec=drawing_spec,
                    connection_drawing_spec=drawing_spec)

    cv2.imshow('Head Pose Estimation', image)
    if cv2.waitKey(5) & 0xFF == 27:
        break
cap.release()

C:\Users\Yassmina Abdo\PycharmProjects\venv\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but SVR was fitted with feature names
  warnings.warn(
C:\Users\Yassmina Abdo\PycharmProjects\venv\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but SVR was fitted with feature names
  warnings.warn(
C:\Users\Yassmina Abdo\PycharmProjects\venv\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but SVR was fitted with feature names
  warnings.warn(
C:\Users\Yassmina Abdo\PycharmProjects\venv\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but SVR was fitted with feature names
  warnings.warn(
C:\Users\Yassmina Abdo\PycharmProjects\venv\lib\site-packages\sklearn\base.py:450: UserWarning: X does not have valid feature names, but SVR was fitted with feature names
  warnings.warn(
C:\Users\Yassmina Abdo\PycharmProjects\venv\lib\site-package